In [1]:
import json
import sys
import re

# function reading the json file 

In [2]:
def read_json_from_file(file_path):
    with open(file_path, 'r') as file:
        return json.load(file)
   
def save_json_to_file(data, filename):
    with open(filename, "w") as f:
        json.dump(data, f,separators=(',', ':'))

In [3]:
import json
import re

def preprocess_json(data):
    # Fix unescaped backslashes
    return re.sub(r'(?<!\\)\\\\', '\\\\', data)

def load_and_clean_json(file_path):
    with open(file_path, 'r') as file:
        lines = file.readlines()

    # Assuming the second line contains JSON
    json_data = lines[1].strip()

    # Preprocess the JSON data before loading
    json_data = preprocess_json(json_data)

    try:
        data = json.loads(json_data)
        return data  # Returning the JSON object
    except json.decoder.JSONDecodeError as e:
        print(f"JSONDecodeError: {e}")
        return None

json2 = load_and_clean_json('database_newend.txt')
#json2 = load_and_clean_json('database_newend.txt')
json1 = load_and_clean_json('database_newstart.txt')


In [4]:
# save_json_to_file(json2, '24250227_135126_end_original_mini.json')
# save_json_to_file(json1, '24250227_135126_start_original_mini.json')
json1=read_json_from_file('cuterun.json')


In [5]:
# # Function to preprocess JSON data
# def preprocess_json1(data):
#     # Fix unescaped backslashes
#     data = re.sub(r'(?<!\\)\\\\', '\\\\', data)  # Correctly escape backslashes

#     # Further custom processing to fix common errors
#     return data
# def load_and_clean_json(file_path):
#     with open(file_path, 'r') as file:
#         lines = file.readlines()

#     # Assuming the second line contains JSON
#     json_data = lines[1].strip()

#     # Preprocess the JSON data before loading
#     json_data = preprocess_json(json_data)

#     try:
#         # Attempt to parse the JSON data
#         data = json.loads(json_data)
#         print("JSON loaded successfully.")
#         return data
#     except json.decoder.JSONDecodeError as e:
#         print(f"JSONDecodeError: {e}")
#         print("Error occurred at position:", e.pos)
#         # Optionally print a snippet of the data around the error
#         print("Data snippet around error:")
#         print(json_data[e.pos - 50:e.pos + 50])  # Print a portion around the error position
#         return None
        
# json2 = load_and_clean_json('database_newend.txt')
# #json1 = load_and_clean_json('database_newstart.txt')

In [9]:
import json

def compare_readback_settings(json_data, target_keys):
    """
    Compare 'Readback' and 'Settings' for specified target keys, only at the same depth.

    Args:
    json_data (dict): JSON object.
    target_keys (list): List of target keys to check in the JSON object.

    Returns:
    dict: Differences between 'Readback' and 'Settings' for the specified keys.
    """

    def compare_dicts(readback, settings):
        """
        Compares 'Readback' and 'Settings' dictionaries and returns the differences.

        Args:
        readback (dict): Readback dictionary.
        settings (dict): Settings dictionary.

        Returns:
        dict: Differences between 'Readback' and 'Settings'.
        """
        diff = {}
        for key in readback:
            if key in settings:
                if readback[key] != settings[key]:
                    diff[key] = {
                        "Readback": readback[key],
                        "Settings": settings[key]
                    }
        return diff

    def recursive_diff(data, parent_key=""):
        diff = {}

        # Only proceed if the key matches one of the target keys
        if any(parent_key.startswith(tk) for tk in target_keys):
            if isinstance(data, dict):
                readback = data.get("Readback")
                settings = data.get("Settings")

                # Only compare if both 'Readback' and 'Settings' are at the same depth
                if readback is not None and settings is not None:
                    key_diff = compare_dicts(readback, settings)
                    if key_diff:
                        diff[parent_key] = key_diff

                # Now recurse deeper into any other sub-level dictionaries, but skip nested 'Settings' or 'Readback'
                for sub_key, sub_value in data.items():
                    if isinstance(sub_value, dict):
                        # Skip keys that are not directly 'Readback' or 'Settings' under the target keys
                        if sub_key not in ["Readback", "Settings"]:
                            nested_diff = recursive_diff(sub_value, parent_key + "." + sub_key)
                            if nested_diff:
                                diff.update(nested_diff)
            else:
                # If it's not a dictionary, compare the values directly
                if data != json_data.get(parent_key):
                    diff[parent_key] = data

        return diff

    return recursive_diff(json_data)


# Example usage:
with open("cuterun.json", "r") as f:
    json_data = json.load(f)

# Define the target keys to check
TARGET_KEYS = [
    "SDU", "Detectors.Det", "Equipment.EBuilder", "Equipment.hvsupply", "Equipment.SDUDriver"
]

# Find differences in 'Readback' and 'Settings' for the specified target keys
differences = compare_readback_settings(json_data, TARGET_KEYS)

# Print results (differences)
print(differences)

# Save results to a file (optional)
with open("differences.json", "w") as f:
    json.dump(differences, f, separators=(',', ':'))  # No indentation to save space


{}


# removing the Keys 

In [5]:
def filter_json_remove_slash_key_value(data, pattern="/key"):
    """
    Recursively removes keys from a dictionary if they contain the given pattern.

    """
    if not isinstance(data, dict):
        return data  # If data is not a dictionary, return as is
    
    new_dict = {}
    for k, v in data.items():
        if pattern not in k:  # Exclude keys that contain the pattern
            if isinstance(v, dict):
                new_dict[k] = filter_json_remove_slash_key_value(v, pattern)  # Recurse for nested dict
            else:
                new_dict[k] = v  # Keep the value as is
    
    return new_dict


In [6]:
json2=filter_json_remove_slash_key_value(json2)
json1=filter_json_remove_slash_key_value(json1)
save_json_to_file(json2, '24250227_135126_end_remove_slash_key_value.json')
save_json_to_file(json1, '24250227_135126_start_remove_slash_key_value.json')

In [ ]:
# def filter_json_remove_slash_key(data, pattern="/key"):
#     # Create a new dictionary to store the filtered results
#     new_dict = {}
    
#     for k, v in data.items():
#         # If the key does not contain the pattern, add it to the new dictionary
#         if pattern not in k:
#             if isinstance(v, dict):
#                 # Recursively apply the function if the value is a dictionary
#                 new_dict[k] = filter_json_remove_slash_key(v, pattern)
#             else:
#                 # Otherwise, just add the key-value pair
#                 new_dict[k] = v
    
#     return new_dict


In [7]:
def filter_json_remove_system_keys(data):
    # Ensure we only modify the 'System' key if it exists
    if 'System' in data:
        # List of keys to remove from 'System'
        keys_to_remove = ['Buffers', 'Transition', 'Flush', 'Tmp']
        
        # Loop through the list and remove each key from 'System' if it exists
        for key in keys_to_remove:
            data['System'].pop(key, None)
    # Filter out entries that have "last_written" in the key
    if isinstance(data, list):  # Check if data is a list of dictionaries
        data = [entry for entry in data if "/last_written" not in entry.get("key", "")]

    return data

In [8]:
def filter_json_remove_legacytrigger(data):
    """
    This function recursively removes keys that match the pattern "/Detectors/DetXX/Settings/LegacyTrigger".
    """
    def recursive_trim(d):
        if isinstance(d, dict):
            # Identify keys matching the specific pattern
            keys_to_remove = [key for key in d if "/Detectors/Det" in key and "/Settings/LegacyTrigger" in key]
            # Remove the matching keys
            for key in keys_to_remove:
                del d[key]
            # Recursively process nested dictionaries or lists
            for key, value in d.items():
                if isinstance(value, (dict, list)):  # If the value is a dictionary or list, apply recursion
                    recursive_trim(value)

    # Call the recursive trim function on the data
    recursive_trim(data)
    
    return data


In [ ]:
# Removing last_readout duplicate time 

In [ ]:
# def filter_data_remove_duplicate_last_written1(data):
#     seen_values = set()  # Stores unique "last_written" values

#     def recurse(d):
#         if isinstance(d, dict):
#             new_dict = {}
#             for k, v in d.items():
#                 if isinstance(v, dict) and "last_written" in v:
#                     last_written_val = v["last_written"]
#                     if last_written_val not in seen_values:
#                         seen_values.add(last_written_val)
#                         new_dict[k] = v  # Keep the first occurrence
#                 else:
#                     # Recursively process nested dictionaries and lists
#                     new_dict[k] = recurse(v)
#             return new_dict
#         elif isinstance(d, list):
#             return [recurse(item) for item in d]
#         return d

#     # First pass to collect duplicates
#     filtered_data = recurse(data)

#     return filtered_data


In [ ]:
# json2 = read_json_from_file('savedata.json')

# json2 = filter_json_remove_slash_key(json2)


# json2 = filter_json_remove_system_keys(json2)


# json2 = filter_json_remove_legacytrigger(json2)


# json2 = json_filter_remove_last_written(json2)
# save_json_to_file(json2, "s")

In [ ]:
# # Function to recursively remove keys ending with "last_written"
# def json_filter_remove_last_written(data):
#     if isinstance(data, dict):
#         return {k: json_filter_remove_last_written(v) for k, v in data.items() if not k.endswith("last_written")}
#     elif isinstance(data, list):
#         return [json_filter_remove_last_written(item) for item in data]
#     return data

In [18]:
import json

def find_paths_with_readback_and_settings(data, path=""):
    """ Recursively find paths containing both 'Readback' and 'Settings'. """
    paths = {}
    if isinstance(data, dict):
        if 'Readback' in data and 'Settings' in data:
            paths[path] = {'Readback': data['Readback'], 'Settings': data['Settings']}
        for key, value in data.items():
            new_path = f"{path}.{key}" if path else key
            paths.update(find_paths_with_readback_and_settings(value, new_path))
    elif isinstance(data, list):
        for index, item in enumerate(data):
            new_path = f"{path}[{index}]"
            paths.update(find_paths_with_readback_and_settings(item, new_path))
    return paths

def compare_readback_and_settings(paths):
    """ Compare 'Readback' and 'Settings' values in the identified paths. """
    differences = {}
    for path, values in paths.items():
        if values['Readback'] != values['Settings']:
            differences[path] = {'Readback': values['Readback'], 'Settings': values['Settings']}
    return differences

def main(json_file):
    with open(json_file, 'r') as file:
        data = json.load(file)
    
    paths = find_paths_with_readback_and_settings(data)
    differences = compare_readback_and_settings(paths)
    
    print("Paths with 'Readback' and 'Settings':")
    for path in paths:
        print(path)
    
    print("\nDifferences in 'Readback' vs 'Settings':")
    for path, diff in differences.items():
        print(f"{path}: Readback++++++++++ = {diff['Readback']}, Settings___________ = {diff['Settings']}")

# Example usage:
main("cuterun.json")


Paths with 'Readback' and 'Settings':
SDU
Detectors.Det01
Detectors.Det02
Detectors.Det03
Detectors.Det04
Detectors.Det05
Detectors.Det06
Detectors.Det07
Equipment.EBuilder
Equipment.hvsupply
Equipment.SDUDriver

Differences in 'Readback' vs 'Settings':
SDU: Readback++++++++++ = {'DAC': {'Current (mA)': [4095, 4095, 4095, 4095], 'Control register': [6, 6, 6, 6], 'Current (mA)/key': {'type': 9, 'num_values': 4, 'access_mode': 7, 'last_written': 1708989024}, 'Control register/key': {'type': 7, 'num_values': 4, 'access_mode': 7, 'last_written': 1708989024}}, 'Antenna': {'ADC Control': 0, 'InputWeights': [239, 255], 'SignalLength': 3, 'AmplGain (dB)': 0, 'BaselineLength': 16, 'ADC Control/key': {'type': 7, 'access_mode': 7, 'last_written': 1708989024}, 'InputWeights/key': {'type': 7, 'num_values': 2, 'access_mode': 7, 'last_written': 1708989024}, 'SignalLength/key': {'type': 7, 'access_mode': 7, 'last_written': 1708989024}, 'AmplGain (dB)/key': {'type': 9, 'access_mode': 7, 'last_written':

In [ ]:
import json

def find_differences(data, parent_key=""):
    """
    Recursively find keys that contain both 'Readback' and 'Settings'
    and keep differences where values are not equal.
    """
    differences = {}

    if isinstance(data, dict):
        if "Readback" in data and "Settings" in data:
            diff = {key: data["Readback"][key] for key in data["Readback"]
                    if key in data["Settings"] and data["Readback"][key] != data["Settings"][key]}
            if diff:  
                differences[parent_key] = diff
        
        for key, value in data.items():
            new_key = f"{parent_key}.{key}" if parent_key else key
            differences.update(find_differences(value, new_key))

    return differences

# Load JSON file
with open("cuterun.json", "r") as f:
    json_data = json.load(f)

TARGET_KEYS = [
    "SDU", "Detectors.Det", "Equipment.EBuilder", "Equipment.hvsupply", "Equipment.SDUDriver"
]

# Find and filter differences
all_differences = find_differences(json_data)
filtered_differences = {key: value for key, value in all_differences.items() if any(key.startswith(tk) for tk in TARGET_KEYS)}
t# Save compact JSON to minimize disk space
with open("differences.json", "w") as f:
    json.dump(filtered_differences, f, separators=(',', ':'))  # No spaces, minimal size


In [9]:
import re
#SDU/Readback
#SDU/Settings

def filter_json_differ_Readback_Setting(d):
    """
    Filters out keys from the 'Settings' section of Detectors/DetXX if they match the values in the 'Readback' section.
    Keeps the keys that differ between the 'Settings' and 'Readback' paths.
    """
    def recurse(d, readback_data, settings_data, path=""):
        """
        Recursive function to traverse and compare the two paths.
        - d: the current data (settings or readback)
        - readback_data: the current data from the Readback section
        - settings_data: the current data from the Settings section
        - path: the current path to compare (for debugging or tracking)
        """
        if isinstance(d, dict):
            # Iterate through the dictionary
            new_dict = {}
            for k, v in d.items():
                new_path = f"{path}/{k}" if path else k
                
                # Check if the path is within the Readback or Settings section
                if re.match(r"/Detectors/Det\d+/Readback", new_path):
                    # If the path starts with Readback, compare values from the 'Settings' section
                    if new_path in settings_data and settings_data[new_path] == v:
                        # If values are the same, remove them from the Settings data
                        settings_data.pop(new_path, None)
                    else:
                        new_dict[k] = recurse(v, readback_data, settings_data, new_path)
                elif re.match(r"/Detectors/Det\d+/Settings", new_path):
                    # Handle the Settings path, keep values only if different from Readback
                    if new_path in readback_data and readback_data.get(new_path) != v:
                        new_dict[k] = v
                    else:
                        # Remove from settings if matched with readback
                        settings_data.pop(new_path, None)
                else:
                    new_dict[k] = recurse(v, readback_data, settings_data, new_path)
            return new_dict
        elif isinstance(d, list):
            return [recurse(item, readback_data, settings_data, f"{path}[{idx}]") for idx, item in enumerate(d)]
        return d

    # Extract readback and settings data from the main structure
    readback_data = d.get('Detectors', {}).get('DetXX', {}).get('Readback', {})
    settings_data = d.get('Detectors', {}).get('DetXX', {}).get('Settings', {})

    # Filter out the matching values and keep differing ones
    filtered_data = recurse(d, readback_data, settings_data)
    #print(filtered_data)
    return filtered_data


In [16]:
json2 = read_json_from_file('24250227_135126_end_original_mini.json')
json2 = filter_json_remove_slash_key_value(json2)
json2 = filter_json_remove_system_keys(json2)
json21 = filter_json_remove_legacytrigger(json2)
print(json21)

{'SDU': {'SDUInfo': {'Enabled': True, 'DriverPort': 5001, 'ReadoutPort': 5002, 'SDUIPAddress': '192.168.1.100'}, 'Readback': {'DAC': {'Current (mA)': [0, 0, 0, 0, 0, 0, 6.0024419], 'Control register': [0, 0, 0, 0]}, 'Antenna': {'AmplGain': 0, 'ADC Control': 288, 'InputWeights': [0, 0], 'SignalLength': 0, 'AmplGain (dB)': 0, 'BaselineLength': 0, 'TriggerDeadtime (us)': 0, 'TriggerThreshold (ADC)': 0}, 'Trigger': {'Trigger_bitsSource': [True, False, False, False, False, False, False, False, False, False, False, False, False]}, 'SDUMessage': {'Broadcast index': 0, 'SDU Message Look up Table': [3, 2, 2, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

In [12]:
json2 = filter_json_differ_Readback_Setting(json2)
print(json2)

{'SDU': {'SDUInfo': {'Enabled': True, 'DriverPort': 5001, 'ReadoutPort': 5002, 'SDUIPAddress': '192.168.1.100'}, 'Readback': {'DAC': {'Current (mA)': [0, 0, 0, 0, 0, 0, 6.0024419], 'Control register': [0, 0, 0, 0]}, 'Antenna': {'AmplGain': 0, 'ADC Control': 288, 'InputWeights': [0, 0], 'SignalLength': 0, 'AmplGain (dB)': 0, 'BaselineLength': 0, 'TriggerDeadtime (us)': 0, 'TriggerThreshold (ADC)': 0}, 'Trigger': {'Trigger_bitsSource': [True, False, False, False, False, False, False, False, False, False, False, False, False]}, 'SDUMessage': {'Broadcast index': 0, 'SDU Message Look up Table': [3, 2, 2, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

In [ ]:
# def find_differences(start_obj, end_obj, parent_key='', differences=None):
#     if differences is None:
#         differences = {}

#     # Get all the unique keys from both objects
#     all_keys = set(start_obj.keys()).union(set(end_obj.keys()))

#     # Iterate through all keys
#     for key in all_keys:
#         # Build the current key's path
#         current_key = parent_key + key

#         # Case where the values are lists
#         if isinstance(start_obj.get(key), list) or isinstance(end_obj.get(key), list):
#             # Compare lists by joining them into a string for easy comparison
#             if str(start_obj.get(key)) != str(end_obj.get(key)):
#                 differences[current_key] = end_obj.get(key)

#         # Case where the values are dictionaries
#         elif isinstance(start_obj.get(key), dict) and isinstance(end_obj.get(key), dict):
#             # Recurse into the nested dictionaries with updated parent_key
#             find_differences(start_obj.get(key), end_obj.get(key), current_key + '/', differences)

#         # Case where the values are primitive types (strings, numbers, etc.)
#         elif start_obj.get(key) != end_obj.get(key):
#             differences[current_key] = end_obj.get(key)

#     return differences

In [29]:
def find_differences(start_obj, end_obj):
    def recursive_diff(start, end):
        diff = {}
        for key in end.keys():
            if key not in start:
                # Key is new in end_obj
                diff[key] = end[key]
            elif isinstance(start[key], dict) and isinstance(end[key], dict):
                # Recursively check nested dictionaries
                nested_diff = recursive_diff(start[key], end[key])
                if nested_diff:  # Only add if there are differences
                    diff[key] = nested_diff
            elif isinstance(start[key], list) and isinstance(end[key], list):
                # Compare lists directly
                if start[key] != end[key]:
                    diff[key] = end[key]
            elif start[key] != end[key]:
                # Value has changed
                diff[key] = end[key]
        return diff

    return recursive_diff(start_obj, end_obj)
# differences = find_differences(start_json, end_json)
# print(differences)


In [14]:
json2 = read_json_from_file('24250227_135126_end_original_mini.json')
json2 = filter_json_remove_slash_key_value(json2)
json2 = filter_json_remove_system_keys(json2)
json2 = filter_json_remove_legacytrigger(json2)
# json2 = filter_json_differ_Readback_Setting(json2)
json1 = read_json_from_file('24250227_135126_start_original_mini.json')
json1 = filter_json_remove_slash_key_value(json1)
json1 = filter_json_remove_system_keys(json1)
# json1 = filter_json_differ_Readback_Setting(json1)
finddifference=find_differences(json2,json1)

In [15]:
finddifference

{'Logger': {'Channels': {'0': {'Settings': {'Current filename': '.RUN00075_DUMP0000.mid.gz'},
    'Statistics': {'Disk level': 0.0015000163269089928,
     'Bytes written': 1048576,
     'Files written': 20816,
     'Events written': 1,
     'Bytes written total': 17319880101925.0,
     'Bytes written subrun': 1048576,
     'Bytes written uncompressed': 17422558}}}},
 'System': {'Clients': {'2049309': {'Run state': 0},
   '2049311': {'Run state': 0}}},
 'Runinfo': {'Stop time': 'Fri Feb 21 15:18:30 2025',
  'Stop time binary': '0x00000000',
  'Transition in progress': 1},
 'Equipment': {'EBlvl': {'Statistics': {'Events sent': 28}},
  'EBuilder': {'Statistics': {'Events sent': 143},
   'Special dump numbers': {'Last BORR': -1, 'Last BORTS': -1}},
  'L2Trigger': {'Statistics': {'Events sent': 33}},
  'readoutfe_SDU': {'Statistics': {'Events sent': 110}},
  'readoutveto03': {'Statistics': {'Events sent': 0}},
  'L2TriggerHistory': {'Statistics': {'Events sent': 5}},
  'readouthistory03': {

In [ ]:
# json2 = filter_json_remove_slash_key(json2)
# json2 = filter_json_remove_system_keys(json2)
# json2 = filter_json_remove_legacytrigger(json2)
# json2 =filter_remove_last_written(json2)
# json2 = filter_json_differ_Readback_Setting(json2)

In [ ]:
#Not Disk space its memory not relevant
# json2 = read_json_from_file('savedata1.json')
# size_in_bytes_comprehensive = asizeof.asizeof(json2)
# size_in_mb = size_in_bytes_comprehensive / (1024)
# # Print size in MB with 3 decimal points
# print(f"Size of json2 : {size_in_mb:.2f} KB")

# json2 = filter_json_remove_slash_key(json2)
# size_in_bytes_comprehensive = asizeof.asizeof(json2)
# size_in_mb = size_in_bytes_comprehensive / (1024)
# print(f"Size of json2 remove /Key : {size_in_mb:.2f} KB")

# json2 = filter_json_remove_system_keys(json2)
# size_in_bytes_comprehensive = asizeof.asizeof(json2)
# size_in_mb = size_in_bytes_comprehensive / (1024)
# print(f"Size of json2 remove system expect client: {size_in_mb:.2f} KB")

# json2 = filter_json_remove_legacytrigger(json2)
# size_in_bytes_comprehensive = asizeof.asizeof(json2)
# size_in_mb = size_in_bytes_comprehensive / (1024)
# print(f"Size of json2 remove legacytrigger: {size_in_mb:.2f} KB")

# json2 =json_filter_remove_last_written(json2)
# size_in_bytes_comprehensive = asizeof.asizeof(json2)
# size_in_mb = size_in_bytes_comprehensive / (1024)
# print(f"Size of json2 remove last written: {size_in_mb:.2f} KB")

# # either way is same remove  not needed
# json2 = filter_json_differ_Readback_Setting(json2)
# size_in_bytes_comprehensive = asizeof.asizeof(json2)
# size_in_mb = size_in_bytes_comprehensive / (1024)
# print(f"Size of json2 remove settings if Readback is same as Detectors/DetXX: {size_in_mb:.2f} KB")

# # either way is same remove 
# size_in_bytes_comprehensive = asizeof.asizeof(finddifference3)
# size_in_mb = size_in_bytes_comprehensive / (1024)
# print(f"Size of json2 remove if start is same as stop: {size_in_mb:.2f} KB")



In [16]:
json2 = read_json_from_file('24250227_135126_end_original_mini.json')
json2 = filter_json_remove_slash_key_value(json2)
save_json_to_file(json2, "24250227_135126_end_remove_slash_key_value.json")
json2 = filter_json_remove_system_keys(json2)
save_json_to_file(json2, "24250227_135126_end_remove_system_keys_except_clients.json")

json2 = filter_json_remove_legacytrigger(json2)
save_json_to_file(json2, "24250227_135126_end_remove_legacytrigger.json")

save_json_to_file(finddifference, "24250227_135126_diff_start_end_ODB.json")

print("saving Json" )

saving Json


In [ ]:
json2 = read_json_from_file('24250227_135126_start_original.json')
json2 = filter_json_remove_slash_key_value(json2)
save_json_to_file(json2, "24250227_135126_start_remove_slash_key_value.json")
json2 = filter_json_remove_system_keys(json2)
save_json_to_file(json2, "24250227_135126_start_remove_system_keys_except_clients.json")

json2 = filter_json_remove_legacytrigger(json2)
save_json_to_file(json2, "24250227_135126_start_remove_legacytrigger.json")
save_json_to_file(finddifference, "24250227_135126_diff_end_withstart_ODB.json")
print("saving start Json" )

In [17]:
import os

# Define file names corresponding to each step with sizes in KB
file_sizes_on_disk = {
    "Original_json": 3728430/1024,
    "Json_removing_slash_key_values": 1669638 / 1024,
    "Json_removing_system_keys_except_clients": 7475285 / 1024,
    "Json_removing_legacytrigger": 1484978 / 1024,
    "Json_difference_in_end_ODB_with_start": 1014/1024
}
print()
# Print table header with better formatting
print(f"{'Action (odb end json for series=24250227_135126)':<50}{'Disk Size (KB)':>20}")
print("=" * 75)

# Print each file's disk size in a neatly formatted way
for file_name, size_kb in file_sizes_on_disk.items():
    print(f"{file_name:<50}{size_kb:>20.2f}")
print()
print()
print()


Action (odb end json for series=24250227_135126)        Disk Size (KB)
Original_json                                                  3641.04
Json_removing_slash_key_values                                 1630.51
Json_removing_system_keys_except_clients                       7300.08
Json_removing_legacytrigger                                    1450.17
Json_difference_in_end_ODB_with_start                             0.99





In [ ]:
# Define file names corresponding to each step with sizes in KB
file_sizes_on_disk = {
    "Original_json": 4335590/1024,
    "Json_removing_slash_key_values": 7795110 / 1024,
    "Json_removing_system_keys_except_clients": 7475284 / 1024,
    "Json_removing_legacytrigger": 7475284 / 1024,
    
}
print()
# Print table header with better formatting
print(f"{'Action (odb start json for series=24250227_135126)':<50}{'Disk Size (KB)':>20}")
print("=" * 75)

# Print each file's disk size in a neatly formatted way
for file_name, size_kb in file_sizes_on_disk.items():
    print(f"{file_name:<50}{size_kb:>20.2f}")
print()
print()
print()

In [20]:
def find_keys_with_settings_and_readback(data):
    matching_keys = [key for key in data.keys() if "Settings" in key and "Readback" in key]
    return matching_keys

In [22]:
json2 = read_json_from_file('24250227_135126_end_original_mini.json')
json2.keys()

dict_keys(['SDU', 'Elog', 'Lazy', 'Alias', 'Alarms', 'Custom', 'DCRCUI', 'Logger', 'System', 'pytest', 'History', 'Runinfo', 'Programs', 'Detectors', 'Equipment', 'Sequencer', 'WebServer', 'ChannelMap', 'Experiment', 'RunControl', 'Seriesinfo', 'TelegraphNoise', 'DetectorTesting', 'DetectorTypeMap', 'HealthMonitoring'])

In [24]:
import json

def find_keys_with_settings_or_readback(data):
    matching_keys = {}

    for key in data.keys():
        if isinstance(data[key], dict):  # Ensure it's a dictionary before checking inside
            sub_keys = data[key].keys()
            if "Settings" in sub_keys or "Readback" in sub_keys:
                matching_keys[key] = [k for k in sub_keys if k in ["Settings", "Readback"]]

    return matching_keys

# Load JSON from file
def read_json_from_file(filename):
    with open(filename, 'r') as f:
        return json.load(f)

# Read JSON
json2 = read_json_from_file('24250227_135126_end_original_mini.json')

# Find top-level keys that contain 'Settings' or 'Readback' inside
matching_keys = find_keys_with_settings_or_readback(json2)

print("Keys containing 'Settings' or 'Readback':", matching_keys)


Keys containing 'Settings' or 'Readback': {'SDU': ['Readback', 'Settings'], 'TelegraphNoise': ['Settings'], 'DetectorTesting': ['Settings']}


In [ ]:
import json

def read_json_with_error_handling(file_path):
    try:
        with open(file_path, 'r', encoding="utf-8") as file:
            return json.load(file)
    except json.JSONDecodeError as e:
        print(f"JSON error at line {e.lineno}, column {e.colno}: {e.msg}")
        return None  # Or handle it as needed
read_json_with_error_handling('database_newend.json')

In [ ]:
import json

def find_settings_and_readback(data, path=""):
    matching_paths = {}

    def search_dict(d, current_path):
        if isinstance(d, dict):
            for key, value in d.items():
                new_path = f"{current_path}.{key}" if current_path else key
                if key in ["Settings", "Readback"]:
                    matching_paths[new_path] = key
                search_dict(value, new_path)  # Recursively search deeper
        elif isinstance(d, list):
            for idx, item in enumerate(d):
                search_dict(item, f"{current_path}[{idx}]")  # Include index for lists

    search_dict(data, path)
    return matching_paths

# Load JSON from file
def read_json_from_file(filename):
    with open(filename, 'r') as f:
        return json.load(f)

# Read JSON
json2 = read_json_from_file('24250227_135126_end_original_mini.json')

# Find all occurrences of 'Settings' and 'Readback'
matching_keys = find_settings_and_readback(json2)

# Print results
for path, key in matching_keys.items():
    print(f"Found '{key}' at: {path}")


# checking readback and Settings Keys 

In [27]:
json2 = read_json_from_file('24250227_135126_end_original_mini.json')
json2 = filter_json_remove_slash_key_value(json2)
json2 = filter_json_remove_system_keys(json2)
json2 = filter_json_remove_legacytrigger(json2)
json12 = json2['SDU']['Readback']
json121 = json2['SDU']['Readback']

In [28]:
#SDU
print(json12.keys())
print(json121.keys())

dict_keys(['DAC', 'Antenna', 'Trigger', 'SDUMessage', 'LEMOOutputs', 'Sync_trigger', 'Accelerometer', 'ReadoutControl', 'ControlAndStatus'])
dict_keys(['DAC', 'Antenna', 'Trigger', 'SDUMessage', 'LEMOOutputs', 'Sync_trigger', 'Accelerometer', 'ReadoutControl', 'ControlAndStatus'])


In [31]:
find_differences(json121,json12)

{}

In [32]:
find_differences(json12,json121)

{}

In [43]:
#Detectors/Det01
Detectors_list = []
for i in range(1,43):
    if i < 10:
        #print("Det0"+str(i))
        Detectors_list.append("Det0"+str(i))
        j1234=json2['Detectors']["Det0"+str(i)]['Readback']
        j123=json2['Detectors']["Det0"+str(i)]['Settings']
        print("Det0"+str(i),'---------------',find_differences(j1234,j123))
    else:
#         print("Det"+str(i))
        Detectors_list.append("Det"+str(i))
        j1234=json2['Detectors']["Det"+str(i)]['Readback']
        j123=json2['Detectors']["Det"+str(i)]['Settings']
        print("Det"+str(i),'++++++++++++++++++++++',find_differences(j1234,j123))


Det01 --------------- {'LED': {'Circulate': False, 'PulseType Comment': '0 = continuous train of pulses, 1 = a single pulse', 'ADCReadoutFilename': './led_adc_readout', 'ADCReadoutFileIndex': 0, 'ADCDownsampling Comment': 'Allowed downsampling factors are 1, 2, 4, 8, 16 and 32', 'ADCReadoutFilename Comment': 'Output file path = {ADCReadoutFilename}_{ADCReadoutFileIndex}.json', 'ADCReadoutFileIndex Comment': 'FileIndex is automatically incremented. Refresh your browser'}, 'Charge': {'Enable(s) Comment': "Both 'AmpPowerEnable' and 'FifteenVPowerEnable' need to be set to 'y' for AmpOffset and Bias values to take effect."}, 'Phonon': {'PreampGain': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1], 'ADCSignal Comment': 'source: n=feedback amp output, y=preamp output', 'ZapEnable Comment': 'SQUID connected to: n=preamp, y=VZap', 'PreampGain Comment': '-6 to 6', 'DriverPGAGain Comment': '1, 2, 4 or 8'}, 'L1Trigger': {'DCRC0': {'LC Coeff Comment': 'Note for the LC Coeff ordering: the first 12 entries are 

KeyError: 'Det25'

In [ ]:
#Detectors/Det01
Detectors_list = []
for i in range(1,43):
    if i < 10:
        #print("Det0"+str(i))
        Detectors_list.append("Det0"+str(i))
    else:
#         print("Det"+str(i))
        Detectors_list.append("Det"+str(i))


In [19]:
import json

def find_readback_and_settings(data, parent_key=""):
    """
    Recursively search for keys 'Readback' and 'Settings' under the same parent key
    and collect their values.

    Args:
        data (dict or list): JSON data structure.
        parent_key (str): Track parent key path.

    Returns:
        list: A list of tuples (full_key_path, readback_value, settings_value)
    """
    results = []
    
    if isinstance(data, dict):
        # Check if both 'Readback' and 'Settings' exist under the same parent
        if 'Readback' in data and 'Settings' in data:
            results.append((parent_key, data['Readback'], data['Settings']))
        
        # Recursively search in nested dictionaries
        for key, value in data.items():
            new_key = f"{parent_key}/{key}" if parent_key else key
            results.extend(find_readback_and_settings(value, new_key))
    
    elif isinstance(data, list):
        # Recursively search in lists
        for index, item in enumerate(data):
            new_key = f"{parent_key}[{index}]"
            results.extend(find_readback_and_settings(item, new_key))
    
    return results

readback_settings = find_readback_and_settings(json21)
for entry in readback_settings:
    print(f"Path: {entry[0]}, Readback: {entry[1]}, Settings: {entry[2]}")


Path: SDU, Readback: {'DAC': {'Current (mA)': [0, 0, 0, 0, 0, 0, 6.0024419], 'Control register': [0, 0, 0, 0]}, 'Antenna': {'AmplGain': 0, 'ADC Control': 288, 'InputWeights': [0, 0], 'SignalLength': 0, 'AmplGain (dB)': 0, 'BaselineLength': 0, 'TriggerDeadtime (us)': 0, 'TriggerThreshold (ADC)': 0}, 'Trigger': {'Trigger_bitsSource': [True, False, False, False, False, False, False, False, False, False, False, False, False]}, 'SDUMessage': {'Broadcast index': 0, 'SDU Message Look up Table': [3, 2, 2, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [33]:
import json

def find_readback_and_settings(data, parent_key=""):
    """
    Recursively search for keys 'Readback' and 'Settings' under the same parent key
    and collect their values.

    Args:
        data (dict or list): JSON data structure.
        parent_key (str): Track parent key path.

    Returns:
        list: A list of tuples (full_key_path, readback_value, settings_value)
    """
    results = []
    
    if isinstance(data, dict):
        # Check if both 'Readback' and 'Settings' exist under the same parent
        if 'Readback' in data and 'Settings' in data:
            results.append((parent_key, data['Readback'], data['Settings']))
        
        # Recursively search in nested dictionaries
        for key, value in data.items():
            new_key = f"{parent_key}/{key}" if parent_key else key
            results.extend(find_readback_and_settings(value, new_key))
    
    elif isinstance(data, list):
        # Recursively search in lists
        for index, item in enumerate(data):
            new_key = f"{parent_key}[{index}]"
            results.extend(find_readback_and_settings(item, new_key))
    
    return results

# Example usage

readback_settings = find_readback_and_settings(json2)
for entry in readback_settings:
    print(f"Path: {entry[0]} /n ______________, Readback: {entry[1]}, -------------------Settings: {entry[2]}")


Path: SDU /n ______________, Readback: {'DAC': {'Current (mA)': [0, 0, 0, 0, 0, 0, 6.0024419], 'Control register': [0, 0, 0, 0]}, 'Antenna': {'AmplGain': 0, 'ADC Control': 288, 'InputWeights': [0, 0], 'SignalLength': 0, 'AmplGain (dB)': 0, 'BaselineLength': 0, 'TriggerDeadtime (us)': 0, 'TriggerThreshold (ADC)': 0}, 'Trigger': {'Trigger_bitsSource': [True, False, False, False, False, False, False, False, False, False, False, False, False]}, 'SDUMessage': {'Broadcast index': 0, 'SDU Message Look up Table': [3, 2, 2, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [10]:
import json

def compare_readback_settings(json_data, target_keys):
    """
    Compare 'Readback' and 'Settings' for specified target keys, only at the same depth.
    Returns both differences and similarities.

    Args:
    json_data (dict): JSON object.
    target_keys (list): List of target keys to check in the JSON object.

    Returns:
    dict: Dictionary containing both differences and similarities between 'Readback' and 'Settings' for the specified keys.
    """

    def compare_dicts(readback, settings):
        """
        Compares 'Readback' and 'Settings' dictionaries and returns both differences and similarities.

        Args:
        readback (dict): Readback dictionary.
        settings (dict): Settings dictionary.

        Returns:
        dict: Differences and similarities between 'Readback' and 'Settings'.
        """
        diff = {}
        similar = {}
        for key in readback:
            if key in settings:
                if readback[key] != settings[key]:
                    diff[key] = {
                        "Readback": readback[key],
                        "Settings": settings[key]
                    }
                else:
                    similar[key] = readback[key]  # If values match, store them as similar
        return diff, similar

    def recursive_diff(data, parent_key=""):
        diff = {}
        similar = {}

        # Only proceed if the key matches one of the target keys
        if any(parent_key.startswith(tk) for tk in target_keys):
            if isinstance(data, dict):
                readback = data.get("Readback")
                settings = data.get("Settings")

                # Only compare if both 'Readback' and 'Settings' are at the same depth
                if readback is not None and settings is not None:
                    key_diff, key_similar = compare_dicts(readback, settings)
                    if key_diff:
                        diff[parent_key] = key_diff
                    if key_similar:
                        similar[parent_key] = key_similar

                # Now recurse deeper into any other sub-level dictionaries, but skip nested 'Settings' or 'Readback'
                for sub_key, sub_value in data.items():
                    if isinstance(sub_value, dict):
                        # Skip keys that are not directly 'Readback' or 'Settings' under the target keys
                        if sub_key not in ["Readback", "Settings"]:
                            nested_diff, nested_similar = recursive_diff(sub_value, parent_key + "." + sub_key)
                            if nested_diff:
                                diff.update(nested_diff)
                            if nested_similar:
                                similar.update(nested_similar)
            else:
                # If it's not a dictionary, compare the values directly
                if data != json_data.get(parent_key):
                    diff[parent_key] = data
                else:
                    similar[parent_key] = data

        return diff, similar

    diff, similar = recursive_diff(json_data)
    return {"Differences": diff, "Similarities": similar}


# Example usage:
with open("cuterun.json", "r") as f:
    json_data = json.load(f)

# Define the target keys to check
TARGET_KEYS = [
    "SDU", "Detectors.Det", "Equipment.EBuilder", "Equipment.hvsupply", "Equipment.SDUDriver"
]

# Find differences and similarities in 'Readback' and 'Settings' for the specified target keys
result = compare_readback_settings(json_data, TARGET_KEYS)

# Print results (differences and similarities)
print("Differences:")
print(result["Differences"])

print("\nSimilarities:")
print(result["Similarities"])

# Save results to a file (optional)
with open("result.json", "w") as f:
    json.dump(result, f, separators=(',', ':'))  # No indentation to save space


Differences:
{}

Similarities:
{}


In [11]:
print(json_data.keys())  # Print top-level keys


dict_keys(['SDU', 'Elog', 'Lazy', 'Alias', 'Alarms', 'Custom', 'Logger', 'System', 'History', 'Runinfo', 'Programs', 'Detectors', 'Equipment', 'Sequencer', 'WebServer', 'ChannelMap', 'Experiment', 'RunControl', 'Seriesinfo', 'CustomScript', 'TelegraphNoise', 'DetectorTesting', 'DetectorTypeMap'])


In [17]:
# json_data['SDU']['Readback']
# json_data['SDU']['Settings']
json_data['Detectors']['Det01'].keys()

dict_keys(['DCRCInfo', 'Readback', 'Settings', 'ReadoutControl', 'BaselineControl', 'DummyReadoutMode', 'InitialUpdateMode', 'ThermometryReadout', 'DummyReadoutMode/key', 'InitialUpdateMode/key', 'StopRunOnTriggerError', 'InitialUpdateMode Comment', 'StopRunOnTriggerError/key', 'InitialUpdateMode Comment/key'])

In [14]:
import json

def compare_readback_settings(json_data, target_keys):
    """
    Compare 'Readback' and 'Settings' for specified target keys, only at the same depth.
    Args:
    json_data (dict): JSON object.
    target_keys (list): List of target keys to check in the JSON object.
    Returns:
    dict: Differences between 'Readback' and 'Settings' for the specified keys.
    """

    def compare_dicts(readback, settings):
        """
        Compares 'Readback' and 'Settings' dictionaries and returns the differences.
        Args:
        readback (dict): Readback dictionary.
        settings (dict): Settings dictionary.
        Returns:
        dict: Differences between 'Readback' and 'Settings'.
        """
        diff = {}
        for key in readback:
            if key in settings:
                if readback[key] != settings[key]:
                    diff[key] = {
                        "Readback": readback[key],
                        "Settings": settings[key]
                    }
        return diff

    def recursive_diff(data, parent_key=""):
        diff = {}

        # Check if the current level matches one of the target keys
        if parent_key in target_keys:
            if isinstance(data, dict):
                readback = data.get("Readback")
                settings = data.get("Settings")

                # Compare only if both 'Readback' and 'Settings' exist
                if readback is not None and settings is not None:
                    key_diff = compare_dicts(readback, settings)
                    if key_diff:
                        diff[parent_key] = key_diff

        # Now recurse into sub-levels of the dictionary
        if isinstance(data, dict):
            for sub_key, sub_value in data.items():
                # Skip comparing 'Readback' and 'Settings' again at this level
                if sub_key not in ["Readback", "Settings"]:
                    nested_diff = recursive_diff(sub_value, parent_key + "." + sub_key)
                    if nested_diff:
                        diff.update(nested_diff)

        return diff

    return recursive_diff(json_data)


# Example usage:
with open("cuterun.json", "r") as f:
    json_data = json.load(f)

# Define the target keys to check
TARGET_KEYS = [
    "SDU", "Detectors.Det", "Equipment.EBuilder", "Equipment.hvsupply", "Equipment.SDUDriver"
]

# Find differences in 'Readback' and 'Settings' for the specified target keys
differences = compare_readback_settings(json_data, TARGET_KEYS)

# Print results (differences)
print("Differences:")
print(differences)

# Save results to a file (optional)
with open("differences.json", "w") as f:
    json.dump(differences, f, separators=(',', ':'))  # No indentation to save space


Differences:
{}


In [21]:
import json

def find_differences(start_obj, end_obj):
    def recursive_diff(start, end):
        diff = {}
        for key in end.keys():
            if key not in start:
                # Key is new in end_obj
                diff[key] = end[key]
            elif isinstance(start[key], dict) and isinstance(end[key], dict):
                # Recursively check nested dictionaries
                nested_diff = recursive_diff(start[key], end[key])
                if nested_diff:  # Only add if there are differences
                    diff[key] = nested_diff
            elif isinstance(start[key], list) and isinstance(end[key], list):
                # Compare lists directly
                if start[key] != end[key]:
                    diff[key] = end[key]
            elif start[key] != end[key]:
                # Value has changed
                diff[key] = end[key]
        return diff

    return recursive_diff(start_obj, end_obj)

# Example usage:
with open("24250227_135126_end_remove_system_keys_except_clients.json", "r") as f:
    json_data = json.load(f)

# Apply the difference finding logic for Readback and Settings under SDU
start_obj = json_data['SDU']['Readback']
end_obj = json_data['SDU']['Settings']

# Find differences between 'Readback' and 'Settings'
differences = find_differences(start_obj, end_obj)

# Print the differences
print("Differences between 'Readback' and 'Settings':")
print(differences)

# Optionally save results to a file
with open("differences_sdu.json", "w") as f:
    json.dump(differences, f, separators=(',', ':'))  # No indentation to save space


Differences between 'Readback' and 'Settings':
{'DAC': {'Current (mA)': [0, 0, 0, 0], 'Control register comment': '0 = disabled. 5 = 4 to 20 mA, 6 =  0 to 20 mA, 7 = 0 to 24 mA.'}, 'Antenna': {'ADC Control Comment': 'Set to 0x120 constantly', 'TriggerDeadtime Comment': 'Minimum interval between antenna triggers in us'}, 'Trigger': {'TriggerSourceComment': 'Accelerometer (0-3), Antenna (4), Lemo (8-11), Ethernet/sync (12). 5-7 not used do not change'}, 'SDUMessage': {'Broadcast index': 255, 'BroadcastComment': 'Choose which index of look-up table to send to DCRCs now.', 'SDU Message Comment': '256 possible SDU responses. 0 = ignore, 1=trigger, 2=start veto, 3=end veto'}, 'LEMOOutputs': {'OutputTypeComment': 'Select between latched output (0) and pulsed output (1) for LEMO 0 and 1', 'Output Pulse Lengths Comment': 'Allowed values are from 0-2.55 micro-seconds in incroments of 10ns', 'WriteFrontPanelOutputsComment': 'A write to bit 0 goes to output 0 and a write to bit 1 goes to output 1'

In [24]:
import json

def find_differences(start_obj, end_obj):
    def recursive_diff(start, end):
        diff = {}
        for key in end.keys():
            if key not in start:
                # Key is new in end_obj
                diff[key] = end[key]
            elif isinstance(start[key], dict) and isinstance(end[key], dict):
                # Recursively check nested dictionaries
                nested_diff = recursive_diff(start[key], end[key])
                if nested_diff:  # Only add if there are differences
                    diff[key] = nested_diff
            elif isinstance(start[key], list) and isinstance(end[key], list):
                # Compare lists directly
                if start[key] != end[key]:
                    diff[key] = end[key]
            elif start[key] != end[key]:
                # Value has changed
                diff[key] = end[key]
        return diff

    return recursive_diff(start_obj, end_obj)

# Example usage:
with open("24250227_135126_end_remove_system_keys_except_clients.json", "r") as f:
    json_data = json.load(f)

# Iterate through all detectors
for detector_key in json_data['Detectors'].keys():
    # Apply the difference finding logic for Readback and Settings under each detector
    start_obj = json_data['Detectors'][detector_key].get('Readback', {})
    end_obj = json_data['Detectors'][detector_key].get('Settings', {})

    # Find differences between 'Readback' and 'Settings' for the specific detector
    differences = find_differences(start_obj, end_obj)

    # Print the differences
    if differences:
        print(f"Differences between 'Readback' and 'Settings' for detector {detector_key}:")
        print(differences)

        # Optionally save results to a file (you can name the file dynamically based on the detector)
        with open(f"differences_{detector_key}.json", "w") as f:
            json.dump(differences, f, separators=(',', ':'))  # No indentation to save space
    else:
        print(f"No differences between 'Readback' and 'Settings' for detector {detector_key}")



Differences between 'Readback' and 'Settings' for detector Det01:
{'LED': {'Circulate': False, 'PulseType Comment': '0 = continuous train of pulses, 1 = a single pulse', 'ADCReadoutFilename': './led_adc_readout', 'ADCReadoutFileIndex': 0, 'ADCDownsampling Comment': 'Allowed downsampling factors are 1, 2, 4, 8, 16 and 32', 'ADCReadoutFilename Comment': 'Output file path = {ADCReadoutFilename}_{ADCReadoutFileIndex}.json', 'ADCReadoutFileIndex Comment': 'FileIndex is automatically incremented. Refresh your browser'}, 'Charge': {'Enable(s) Comment': "Both 'AmpPowerEnable' and 'FifteenVPowerEnable' need to be set to 'y' for AmpOffset and Bias values to take effect."}, 'Phonon': {'PreampGain': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1], 'ADCSignal Comment': 'source: n=feedback amp output, y=preamp output', 'ZapEnable Comment': 'SQUID connected to: n=preamp, y=VZap', 'PreampGain Comment': '-6 to 6', 'DriverPGAGain Comment': '1, 2, 4 or 8'}, 'L1Trigger': {'DCRC0': {'LC Coeff Comment': 'Note for the 

In [25]:
import json

# Example TARGET_KEYS list containing paths to look for
TARGET_KEYS = [
    "SDU", 
    "Detectors.Det", 
    "Equipment.EBuilder", 
    "Equipment.hvsupply", 
    "Equipment.SDUDriver"
]

# Function to find the keys and their paths containing 'Readback' and 'Settings'
def find_keys_with_readback_settings(json_data, target_keys):
    found_keys = []

    # Iterate over all the target paths
    for path in target_keys:
        keys = path.split('.')  # Split path to access sub-keys
        current_data = json_data
        path_so_far = []  # To keep track of the path

        # Traverse the nested structure to reach the target dictionary
        for key in keys:
            if key in current_data:
                current_data = current_data[key]
                path_so_far.append(key)
            else:
                break  # If path doesn't exist, stop looking deeper

        # Check if 'Readback' and 'Settings' are found in this part of the JSON structure
        if isinstance(current_data, dict):
            for sub_key in ['Readback', 'Settings']:
                if sub_key in current_data:
                    found_keys.append('.'.join(path_so_far + [sub_key]))
    
    return found_keys

# Load your JSON data
with open("cuterun.json", "r") as f:
    json_data = json.load(f)

# Find and print all keys with 'Readback' or 'Settings' in the specified paths
found_keys = find_keys_with_readback_settings(json_data, TARGET_KEYS)

# Print the found keys and their paths
if found_keys:
    print("Found the following keys with 'Readback' or 'Settings':")
    for key in found_keys:
        print(key)
else:
    print("No keys with 'Readback' or 'Settings' were found in the specified paths.")


Found the following keys with 'Readback' or 'Settings':
SDU.Readback
SDU.Settings
Equipment.EBuilder.Readback
Equipment.EBuilder.Settings
Equipment.hvsupply.Readback
Equipment.hvsupply.Settings
Equipment.SDUDriver.Readback
Equipment.SDUDriver.Settings


In [27]:
import json

def find_differences(start_obj, end_obj):
    def recursive_diff(start, end):
        diff = {}
        for key in end.keys():
            if key not in start:
                # Key is new in end_obj
                diff[key] = end[key]
            elif isinstance(start[key], dict) and isinstance(end[key], dict):
                # Recursively check nested dictionaries
                nested_diff = recursive_diff(start[key], end[key])
                if nested_diff:  # Only add if there are differences
                    diff[key] = nested_diff
            elif isinstance(start[key], list) and isinstance(end[key], list):
                # Compare lists directly
                if start[key] != end[key]:
                    diff[key] = end[key]
            elif start[key] != end[key]:
                # Value has changed
                diff[key] = end[key]
        return diff

    return recursive_diff(start_obj, end_obj)

# Example usage:
with open("24250227_135126_end_remove_system_keys_except_clients.json", "r") as f:
    json_data = json.load(f)

# Define the target keys you found (replace these with actual found paths)
target_keys = [
    "SDU", 
    "Equipment.EBuilder", 
    "Equipment.hvsupply", 
    "Equipment.SDUDriver"
]

# Loop through each key path, comparing 'Readback' and 'Settings'
differences_all = {}

for key in target_keys:
    # Split path to access sub-keys (SDU, Equipment.EBuilder, etc.)
    keys = key.split('.')  # Split path to access sub-keys
    current_data = json_data

    # Traverse the nested structure to reach the target dictionary
    for sub_key in keys:
        if sub_key in current_data:
            current_data = current_data[sub_key]
        else:
            break  # If path doesn't exist, stop looking deeper
    
    # Now current_data should be the dictionary under the current key
    if isinstance(current_data, dict):
        # Ensure that both Readback and Settings exist
        if "Readback" in current_data and "Settings" in current_data:
            start_obj = current_data['Readback']
            end_obj = current_data['Settings']
            
            # Find differences between 'Readback' and 'Settings'
            differences = find_differences(start_obj, end_obj)
            
            # Only save differences if they exist
            if differences:
                differences_all[key] = differences

# Print the differences for all paths
print("Differences between 'Readback' and 'Settings' for the following keys:")
for key, diff in differences_all.items():
    print(f"\nKey: {key}")
    print(json.dumps(diff, indent=2))  # Pretty print differences

# Optionally, save results to a file
with open("differences_all.json", "w") as f:
    json.dump(differences_all, f, indent=2)  # Indented JSON for readability


Differences between 'Readback' and 'Settings' for the following keys:

Key: SDU
{
  "DAC": {
    "Current (mA)": [
      0,
      0,
      0,
      0
    ],
    "Control register comment": "0 = disabled. 5 = 4 to 20 mA, 6 =  0 to 20 mA, 7 = 0 to 24 mA."
  },
  "Antenna": {
    "ADC Control Comment": "Set to 0x120 constantly",
    "TriggerDeadtime Comment": "Minimum interval between antenna triggers in us"
  },
  "Trigger": {
    "TriggerSourceComment": "Accelerometer (0-3), Antenna (4), Lemo (8-11), Ethernet/sync (12). 5-7 not used do not change"
  },
  "SDUMessage": {
    "Broadcast index": 255,
    "BroadcastComment": "Choose which index of look-up table to send to DCRCs now.",
    "SDU Message Comment": "256 possible SDU responses. 0 = ignore, 1=trigger, 2=start veto, 3=end veto"
  },
  "LEMOOutputs": {
    "OutputTypeComment": "Select between latched output (0) and pulsed output (1) for LEMO 0 and 1",
    "Output Pulse Lengths Comment": "Allowed values are from 0-2.55 micro-seconds